### Setup

I set my notebook environment so that it outputs the value of the last line of code 
if it is an expression *or* an assignment. By default, it only prints expressions.

In [1]:
%config InteractiveShell.ast_node_interactivity = 'last_expr_or_assign'

In [2]:
12 + 34

46

In [3]:
# this would have no output with 'last_expr' interactivity
a = 12 + 34

46

### Downloading Data

In [26]:
query = """SELECT
  `inspection_id`,
  `dba_name`,
  `aka_name`,
  `license_`,
  `facility_type`,
  `risk`,
  `address`,
  `city`,
  `state`,
  `zip`,
  `inspection_date`,
  `inspection_type`,
  `results`,
  `violations`,
  `latitude`,
  `longitude`,
  `location`
WHERE `inspection_id` BETWEEN 2000000 AND 2500000"""

'SELECT\n  `inspection_id`,\n  `dba_name`,\n  `aka_name`,\n  `license_`,\n  `facility_type`,\n  `risk`,\n  `address`,\n  `city`,\n  `state`,\n  `zip`,\n  `inspection_date`,\n  `inspection_type`,\n  `results`,\n  `violations`,\n  `latitude`,\n  `longitude`,\n  `location`\nWHERE `inspection_id` BETWEEN 2000000 AND 2500000'

In [37]:
import urllib.request
import gzip
from pathlib import Path

p = Path('Food_Inspections.csv.gz')
if not p.exists():
    url = "https://data.cityofchicago.org/api/v3/views/4ijn-s7e5/export.csv?"
    params = {
        'query': query
    }
    encoded_params = urllib.parse.urlencode(params)
    # print(url + encoded_params)
    request = urllib.request.Request(url + encoded_params)
    request.add_header('accept-encoding', 'gzip')
    request.add_header('X-App-Token', 'y7gDTnNk91kMx9mjQ7WAY8WfK')
    with urllib.request.urlopen(request) as response:
        if response.info().get('Content-Encoding') == 'gzip':
            with open(p,'wb') as f:
                f.write(response.read())
        else:
            with gzip.open(p,'wb') as f:
                f.write(response.read())

### Loading Data

In [38]:
import gzip
import csv
r = csv.DictReader(gzip.open(p,'rt'))

In [39]:
# store everything in memory so we can iterate over it many times
data = list(r);

In [40]:
data[0]

{'Inspection ID': '2170232',
 'DBA Name': 'Canter Middle',
 'AKA Name': 'Canter Middle',
 'License #': '23981',
 'Facility Type': 'School',
 'Risk': 'Risk 2 (Medium)',
 'Address': '4959 S Blackstone (1500E) ',
 'City': 'CHICAGO',
 'State': 'IL',
 'Zip': '60615',
 'Inspection Date': '09/28/2021',
 'Inspection Type': 'Canvass',
 'Results': 'Pass',
 'Violations': '',
 'Latitude': '41.80434474043',
 'Longitude': '-87.59039493829',
 'Location': '(41.8043447404251, -87.5903949382913)'}

In [41]:
{row['Results'] for row in data}

{'Business Not Located',
 'Fail',
 'No Entry',
 'Not Ready',
 'Out of Business',
 'Pass',
 'Pass w/ Conditions'}

In [42]:
from collections import Counter
Counter(row['Results'] for row in data)

Counter({'Pass': 27261,
         'Pass w/ Conditions': 19479,
         'Fail': 13687,
         'Out of Business': 5483,
         'No Entry': 3664,
         'Not Ready': 1712,
         'Business Not Located': 12})

In [43]:
# filter for all failed inspections
failed = [row for row in data if row['Results'] == "Fail"];

In [44]:
len(failed)

13687

In [45]:
# look at first failed inspection
failed[0]

{'Inspection ID': '2498205',
 'DBA Name': 'PHO NUMBER 1- VIETNAMESE CUISINE LLC',
 'AKA Name': 'PHO NUMBER 1- VIETNAMESE CUISINE',
 'License #': '2333891',
 'Facility Type': 'Restaurant',
 'Risk': 'Risk 1 (High)',
 'Address': '5914 W LAWRENCE AVE ',
 'City': 'CHICAGO',
 'State': 'IL',
 'Zip': '60630',
 'Inspection Date': '04/14/2021',
 'Inspection Type': 'Canvass',
 'Results': 'Fail',
 'Violations': '36. THERMOMETERS PROVIDED & ACCURATE - Comments: OBSERVED NO METAL STEM THERMOMETER ON SITE FOR TAKING INTERNAL TEMPERATURES OF TCS FOODS. INSTRUCTED TO PROVIDE. PRIORITY FOUNDATION VIOLATION 7-38-005. CITATION ISSUED.  | 53. TOILET FACILITIES: PROPERLY CONSTRUCTED, SUPPLIED, & CLEANED - Comments: OBSERVED NO COVERED TRASH RECEPTACLE INSIDE CUSTOMER TOILET ROOM. INSTRUCTED TO PROVIDE. ',
 'Latitude': '41.96778735334',
 'Longitude': '-87.77542758599',
 'Location': '(41.967787353343006, -87.77542758598545)'}

In [46]:
# count up which establishments have highest numbers of failures
c = Counter(row['DBA Name'] for row in data)
c.most_common(20)

[('SUBWAY', 956),
 ('DUNKIN DONUTS', 575),
 ("MCDONALD'S", 152),
 ('7-ELEVEN', 113),
 ('CHIPOTLE MEXICAN GRILL', 109),
 ('DUNKIN DONUTS/BASKIN ROBBINS', 108),
 ('POTBELLY SANDWICH WORKS LLC', 102),
 ('POTBELLY SANDWICH WORKS', 99),
 ('WINGSTOP', 98),
 ('TACO BELL', 94),
 ('FRESHII', 90),
 ('CHARTWELLS', 90),
 ('MCDONALDS', 87),
 ("JIMMY JOHN'S", 84),
 ('CORNER BAKERY CAFE', 80),
 ('CITGO', 80),
 ('JIMMY JOHNS', 78),
 ("WENDY'S PROPERTIES, LLC", 78),
 ('KENTUCKY FRIED CHICKEN', 78),
 ('WHOLE FOODS MARKET', 73)]